In [55]:
#Jakub Wlodarczyk 305064
import numpy as np
import numba
from numba import typed
import matplotlib.pyplot as plt
from pickletools import optimize
import tqdm
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

In [56]:
# PARAMETRY WEJSCIOWE
N=1000
J=1
Beta=4e5
B=1.9
Steps=100
Dens=0.2

In [57]:
#wyliczenie energii
@numba.njit(numba.int64(numba.int64, numba.int64))
def calculate_energy(S0, Sn): 
        return 2 * S0 * (B + J * Sn)

In [58]:
#obliczenie siatki
@numba.njit(numba.int32(numba.int32[:,:], numba.int64, numba.int64))
def calculate_system(system, i, j):

    #warunki brzegowe
    Sn = system[(i - 1) % N, j] + system[(i + 1) % N, j] + system[i, (j - 1) % N] + system[i, (j + 1) % N]

    dE = calculate_energy(system[i, j], Sn)

    if dE < 0 or np.random.random() < np.exp(-dE*Beta):    #zmiana wartosci spinu przy okreslonych warunkach
        system[i, j] = -system[i, j]

    return system[i, j]

In [59]:
#zmiana losowego spinu w siatce
@numba.njit()
def change_system(system):

    for _ in range(N*N):
        
        #biore losowy spin
        i = np.random.randint(N)
        j = np.random.randint(N)

        system[i,j] = calculate_system(system, i, j)

In [60]:
#run symulacji
def run_simulation(steps):   
    system=np.random.choice([1, -1], [N, N], p=[Dens, 1-Dens])    

    tab_system = typed.List()
    tab_system.append(system.copy())

    for _ in range(steps):
        change_system(system)

        tab_system.append(system.copy())

    return tab_system

In [61]:
tab_system = run_simulation(Steps)

#bez numby 20 minut 44.9 sekund
#z numba 10.9 sekund

In [62]:
fig, ax = plt.subplots(figsize = (5, 5))
fig.subplots_adjust(0, 0, 1, 1)
img = ax.imshow(tab_system[0])

plt.close()

def frame(i):
    img.set_data(tab_system[i])
    return img,

plt.rcParams['animation.embed_limit'] = 2**128

anim = FuncAnimation(fig, frame, frames = len(tab_system), interval = 200, blit = True)
HTML(anim.to_jshtml())